In [1]:
from mace.calculators import mace_mp
from ase import build

from ase.md import Langevin
from ase.md.velocitydistribution import MaxwellBoltzmannDistribution
from ase import units


macemp = mace_mp() # return ASE calculator
atoms = build.molecule('H2O')
descriptors_mp = macemp.get_descriptors(atoms)

Using Materials Project MACE for MACECalculator with /Users/joehart/.cache/mace/5yyxdm76
Using float32 for MACECalculator, which is faster but less accurate. Recommended for MD. Use float64 for geometry optimization.
Default dtype float32 does not match model dtype float64, converting models to float32.


In [26]:
from ase.md import Langevin
from ase.md.velocitydistribution import MaxwellBoltzmannDistribution
from ase import units

atoms.calc = macemp

# Initialize velocities.
T_init = 300  # Initial temperature in K
MaxwellBoltzmannDistribution(atoms, T_init * units.kB)

# Set up the Langevin dynamics engine for NVT ensemble.
dyn = Langevin(atoms, 0.5 * units.fs, T_init * units.kB, 0.001)
n_steps = 100 # Number of steps to run
dyn.run(n_steps)

/Users/joehart/opt/anaconda3/lib/python3.8/site-packages/ase/md/md.py:53: FutureWarning: Specify the temperature in K using the 'temperature_K' argument
  warnings.warn(FutureWarning(w))


True

In [3]:
from ase.io.trajectory import Trajectory

def printenergy(a=atoms):
    """Function to print the potential, kinetic and total energy"""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)
    print('Energy per atom: Epot = %.3feV  Ekin = %.3feV (T=%3.0fK)  '
          'Etot = %.3feV' % (epot, ekin, ekin / (1.5 * units.kB), epot + ekin))
    
atoms.calc = macemp

T_init = 300  # Initial temperature in K
MaxwellBoltzmannDistribution(atoms, T_init * units.kB)

# Set up the Langevin dynamics engine for NVT ensemble.
dyn = Langevin(atoms, 0.5 * units.fs, T_init * units.kB, 0.001)
n_steps = 100 # Number of steps to run

dyn.attach(printenergy, interval = 2) # observer: attach the printenergy function to the dynamics

traj = Trajectory('H2O.traj', 'w', atoms) # save the trajectory
dyn.attach(traj.write, interval = 10) # write the trajectory to file
printenergy()
dyn.run(n_steps)


Energy per atom: Epot = -4.720eV  Ekin = 0.100eV (T=777K)  Etot = -4.619eV
Energy per atom: Epot = -4.720eV  Ekin = 0.100eV (T=777K)  Etot = -4.619eV
Energy per atom: Epot = -4.719eV  Ekin = 0.099eV (T=768K)  Etot = -4.619eV
Energy per atom: Epot = -4.716eV  Ekin = 0.097eV (T=750K)  Etot = -4.619eV
Energy per atom: Epot = -4.713eV  Ekin = 0.094eV (T=727K)  Etot = -4.619eV
Energy per atom: Epot = -4.711eV  Ekin = 0.092eV (T=710K)  Etot = -4.620eV
Energy per atom: Epot = -4.710eV  Ekin = 0.090eV (T=698K)  Etot = -4.619eV
Energy per atom: Epot = -4.709eV  Ekin = 0.090eV (T=699K)  Etot = -4.619eV
Energy per atom: Epot = -4.711eV  Ekin = 0.092eV (T=713K)  Etot = -4.619eV
Energy per atom: Epot = -4.714eV  Ekin = 0.095eV (T=736K)  Etot = -4.619eV
Energy per atom: Epot = -4.718eV  Ekin = 0.099eV (T=762K)  Etot = -4.619eV
Energy per atom: Epot = -4.719eV  Ekin = 0.099eV (T=768K)  Etot = -4.620eV
Energy per atom: Epot = -4.719eV  Ekin = 0.099eV (T=766K)  Etot = -4.620eV
Energy per atom: Epot = -

True

In [9]:
from ase.visualize import view

view(atoms, viewer='x3d')

In [6]:
from ase import Atoms
from ase.io import read

# Load the CIF file
atoms = read("/Users/joehart/Desktop/0_Cambridge/0_MPhil_Scientific_Computing/Written_assignments/MACE-MP-0/Notebooks_mace/mace_test/SrLiH3.cif")

# Print basic structure info
print(atoms)


Atoms(symbols='SrLiH3', pbc=True, cell=[4.630791, 4.630791, 4.630791], spacegroup_kinds=...)


In [8]:
from ase.visualize import view
view(atoms, viewer='x3d')

In [3]:
from ase import Atoms
from ase.build import bulk
from ase.optimize import BFGS
from mace.calculators import mace_mp
import numpy as np

# Function to create perovskite structures
def create_perovskite(lattice_constant, center_atom):
    """Creates a cubic perovskite SrXH3 structure with space group Pm-3m."""
    atoms = Atoms(
        symbols=["Sr", center_atom, "H", "H", "H"],
        positions=[
            [0, 0, 0],  # Sr at (0,0,0)
            [0.5, 0.5, 0.5],  # Li or Zn at (0.5,0.5,0.5)
            [0.5, 0.5, 0],  # H at (0.5,0.5,0)
            [0.5, 0, 0.5],  # H at (0.5,0,0.5)
            [0, 0.5, 0.5]   # H at (0,0.5,0.5)
        ],
        cell=np.eye(3) * lattice_constant,  # Cubic unit cell
        pbc=True  # Periodic boundary conditions
    )
    return atoms

# Create structures for SrLiH3 and SrZnH3
srlih3 = create_perovskite(lattice_constant=3.9, center_atom="Li")
srznh3 = create_perovskite(lattice_constant=3.81, center_atom="Zn")


srlih3.calc = mace_mp()
srznh3.calc = mace_mp()

# Optimize geometry using BFGS
optimizer_li = BFGS(srlih3)
optimizer_li.run(fmax=0.02)  # Converge at forces < 0.02 eV/Å

optimizer_zn = BFGS(srznh3)
optimizer_zn.run(fmax=0.02)

# Save CIF files
srlih3.write("SrLiH3_optimized.cif")
srznh3.write("SrZnH3_optimized.cif")

# Print final structure info
print("SrLiH3 optimized structure:", srlih3)
print("SrZnH3 optimized structure:", srznh3)

Using Materials Project MACE for MACECalculator with /Users/joehart/.cache/mace/5yyxdm76
Using float32 for MACECalculator, which is faster but less accurate. Recommended for MD. Use float64 for geometry optimization.
Default dtype float32 does not match model dtype float64, converting models to float32.
Using Materials Project MACE for MACECalculator with /Users/joehart/.cache/mace/5yyxdm76
Using float32 for MACECalculator, which is faster but less accurate. Recommended for MD. Use float64 for geometry optimization.
Default dtype float32 does not match model dtype float64, converting models to float32.
      Step     Time          Energy          fmax
BFGS:    0 23:15:55    14860.742188   131015.089207
BFGS:    1 23:15:56      540.177856     4513.943287
BFGS:    2 23:15:56     2764.728760    19262.109542
BFGS:    3 23:15:56     1924.765015    14058.059041
BFGS:    4 23:15:57     3159.344482    33510.324140
BFGS:    5 23:15:57    17784.638672   294641.069995
BFGS:    6 23:15:57    10452

KeyboardInterrupt: 